## This document performs the data preprocessing of toronto yelp data 

In [1]:
from ast import literal_eval
from os import listdir
from os.path import isfile, join
from scipy.sparse import csr_matrix, load_npz, save_npz
from tqdm import tqdm
from sklearn.preprocessing import normalize
import yaml
import seaborn as sns
import datetime
import json
import numpy as np
import pandas as pd
import time
import yaml
import scipy.sparse as sparse
from ast import literal_eval

# For Python2 this have to be done
# from __future__ import division


### Import Toronto data as df,  userJson as df_user

In [2]:
# read csv data reviews 
df_toronto_review = pd.read_csv('../data/toronto_reviews.csv')

# read business csv data 
df_business = pd.read_csv('../data/businesses_final_toronto.csv')

In [3]:
df_toronto_review.head(2)

Unnamed: 0  Unnamed: 0.1             business_id  friend_count  ghost  \
0           0             0  bSQGCheX1BwvL67Az1OJlA            90  False   
1           1             1  bSQGCheX1BwvL67Az1OJlA             0  False   

  img_dsc img_url     nr  photo_count  rating  ...  review_language  \
0      []      []  False        231.0     5.0  ...               en   
1      []      []  False          9.0     1.0  ...               en   

                                         review_text          ufc  \
0  I had a good experience at this store. I was g...  [10, 1, 10]   
1  I reaaaaaally wish I had read all the stories ...    [0, 0, 0]   

                  user_id         user_loc vote_count Updated  Year  Month  \
0  q41qqkChL9fRxF43cnkgbw      Houston, TX       11.0   False  2018      5   
1  tNT5I9-QcljS-7w_doXCXQ  Toronto, Canada        0.0   False  2018      6   

   Day  
0    9  
1    3  

[2 rows x 23 columns]

In [4]:
# rename business id
df_business.rename(columns={'id': 'business_id'}, inplace=True)

In [10]:
df_business.image_url[33]

'https://s3-media2.fl.yelpcdn.com/bphoto/u8cnVz3jgvlNxrB45OKHcQ/o.jpg'

In [6]:
df_business.head(2)

Unnamed: 0                    alias  \
0           0    the-ossington-toronto   
1           1  life-is-sweet-toronto-3   

                                          categories  \
0      [{'alias': 'divebars', 'title': 'Dive Bars'}]   
1  [{'alias': 'desserts', 'title': 'Desserts'}, {...   

                                         coordinates    display_phone  \
0      {'latitude': 43.6456, 'longitude': -79.41903}  +1 416-850-0161   
1  {'latitude': 43.67212500034, 'longitude': -79....  +1 416-698-0555   

      distance             business_id  \
0  4831.221092  KUdj08tVC3tvIT0rM6V8uQ   
1  1716.906703  rnjFHvb1I-KlnGvv_o_Zxg   

                                           image_url  is_closed  \
0  https://s3-media1.fl.yelpcdn.com/bphoto/dEQPAb...      False   
1  https://s3-media2.fl.yelpcdn.com/bphoto/s11QxZ...      False   

                                            location           name  \
0  {'address1': '61 Ossington Avenue', 'address2'...  The Ossington   
1  {'address1': '2345 Queen Street E', 'address2'...  Life is Sweet   

          phone price  rating  review_count transactions  \
0  1.416850e+10    $$     3.0            46           []   
1  1.416698e+10    $$     4.0            10           []   

                                                 url  
0  https://www.yelp.com/biz/the-ossington-toronto...  
1  https://www.yelp.com/biz/life-is-sweet-toronto...

In [7]:
print("total business numbers:", len(df_business))

total business numbers: 32123


In [8]:
restaurantString = "restaurant|Bar|Bakeries|food|Coffee|Tea|Waffles|Desserts\
|sandwiches|Cupcakes|cafes|Breakfast|Brunch|Lunch|Dinner|chicken|wings\
|singaporean|malaysian|indonesian|russian|taiwanese|american|vietnamese|moroccan\
|cantonese|caribbean|mideastern|asian|italian|korean|himalayan|african|nepalese|laotian|sushi|hawaiian\
|mediterranean|caterers|fish|chips|fishnchips|thai|salad|chinese|seafood|irish|portuguese|french|vegan|raw_food\
|pizza|latin|lebanese|burgers|gluten-free|japanese|pakistani|mexican|sushi|argentine|lounges|barbeque\
|canadian|dimsum|halal|afghan|donuts|juice|smoothies|bagels|ramen|icecream|pubs|falafel\
|noodles|soup|cheese|colombian|turkish|ethiopian|peruvian|hungarian|ukrainian|indian\
|persian|brazilian|vegetarian|austrian|arabian|haitian|cambodian|german|greek|Barbeque|Buffets\
|Cajun/Creole|Cajun|Cuban|Czech|Delis|Diners|Filipino|Festivals|Hot Dogs|Hot Pot|Macarons|Modern European\
|Nightlife|Salvadoran|Venezuelan"

# We only take restaurant business with the above keywords
cond_category_restaurant = df_business["categories"].str.contains(restaurantString,case=False)

#df_business_Restaurant = df_business[cond_category_restaurant]
df_matched_business = df_business[cond_category_restaurant]

#Now filter out groceries, acupuncture 
filterString = "acupuncture|grocery|bookstores|musicvideo|yoga|servicestations|convenience|homeappliancerepair\
|appliances|Repair|bike|repair|Used|toys|wholesale|supplies|hair|barbers|Hair Salons|Archery|Adult Entertainment|Amateur Sports Teams\
|Airport Lounges|Vinyl Records|Pilates|fitness|Real Estate Agents|Real Estate Services|Recreation Centers|Reflexology\
|massage|Tattoo|Traditional Chinese Medicine|Trainers|Walking Tours|Virtual Reality Centers|Musical Instrument Services|Laser Tag\
|Community Service/Non-Profit|Flea Markets|Tours|Golf|Hotels|Kids Activities"

df_business_Restaurant = df_matched_business[~df_matched_business["categories"].str.contains(filterString,case=False)]

print('Matched categories, before filtering size: ', len(df_matched_business))
print('Matched categories, after filtering size: ', len(df_business_Restaurant))

Matched categories, before filtering size:  10115
Matched categories, after filtering size:  9387


In [9]:
#Checking the filtered out businesses at the first step to see if missed any restaurants

cond_category_Not_restaurant = ~df_business["categories"].str.contains(restaurantString,case=False)
business_not_res = df_business[cond_category_Not_restaurant]
# for index, value in business_not_res['categories'].items():
#     print("Index : {}, Value : {}".format(index, value))

### Run this sell to check filtered out restaurants

In [10]:
# cat_set = []
# for cat in tqdm(business_not_res.categories.values):
#     temp = yaml.safe_load(cat)
# #     ans.append([temp[i]["title"] for i in range(len(temp))])
    
#     #loop through key, append title as categories 
#     for i in tqdm(range(len(temp))):
#         cat_set.append(temp[i]["title"])
# set(cat_set)

In [11]:
#Checking invalid businesses
#pd.options.display.max_colwidth = 90  
#set(df_business_Restaurant[df_business_Restaurant["categories"].str.contains('Qi Gong',case=False)].categories)

#checking original missed restaurants
#Czech
#df_business[df_business["categories"].str.contains('Venezuelan',case=False)]

In [12]:
# for index in range(0,100):
#     print(business_not_res['categories'][index])
#business_not_res['categories']

# for index, value in business_not_res['categories'].items():
#     print("Index : {}, Value : {}".format(index, value))

In [13]:
#Checking business name
# df_business['name'][31600]

In [14]:
# Drop duplicate values in df_business
print(len(df_business_Restaurant))
df_business_clean = df_business_Restaurant.drop_duplicates(subset ="business_id", 
                     keep = False)
print(len(df_business_clean))
df_business_clean = df_business_clean.reset_index()

9387
9387


## Separate out longitude and altitude

In [15]:
latitudeList = []
longitudeList = []

for business in range(len(df_business_clean)):
    latitude= yaml.safe_load(df_business_clean.coordinates[business])['latitude']
    longitude = yaml.safe_load(df_business_clean.coordinates[business])['longitude']
    latitudeList.append(latitude)
    longitudeList.append(longitude)

In [16]:
df_latitude = pd.DataFrame(np.asarray(latitudeList))
df_latitude.rename(columns={0: "latitude"}, inplace = True)
df_longitude = pd.DataFrame(np.asarray(longitudeList))
df_longitude.rename(columns={0: "longitude"}, inplace = True)

In [17]:
df_business_clean["latitude"] = df_latitude
df_business_clean["longitude"] = df_longitude
df_business_clean = df_business_clean.drop(df_business_clean[df_business_clean['longitude'] == 'None'].index)
df_business_clean = df_business_clean.drop(df_business_clean[df_business_clean['latitude'] == 'None'].index)
df_business_clean = df_business_clean.reset_index()

## Changing the format of category

In [18]:
# Rename Month as Day and Day as Month(error occurs on original data)
df_toronto_review=df_toronto_review.rename(columns = {'Month':'new_Day'})
df_toronto_review=df_toronto_review.rename(columns = {'Day':'Month'})
df_toronto_review=df_toronto_review.rename(columns = {'new_Day':'Day'})

In [19]:
# df_toronto_review.shape

In [20]:
# df_business_clean.shape

### Merging review and business data 

In [21]:
# inner join two full dataset
df = pd.merge(df_toronto_review, df_business_clean, on='business_id', how='inner')

In [22]:
df.shape

(501473, 43)

In [23]:
# merge the date and turn it into string
df['date'] = pd.to_datetime(df[['Year', 'Month','Day']])
df['date'] = df['date'].astype(str)

In [24]:
# rename the columns to match the algorithm 
df.rename(columns={'rating_x': 'stars','rating_y': 'business_stars','review_text': 'text',}, inplace=True)

In [25]:
# get rid of the rows without user_id
df = df[~df["user_id"].isnull()]

In [26]:
pd.set_option('display.max_columns', None)
df.head(2)

Unnamed: 0_x  Unnamed: 0.1             business_id  friend_count  ghost  \
0             6             6  Xo1LNzhnwE-ilqsM3ybs9Q           105  False   
1             7             7  Xo1LNzhnwE-ilqsM3ybs9Q           171  False   

                                             img_dsc  \
0  ['Photo of Happy Lemon - Markham, ON, Canada. ...   
1  ['Photo of Happy Lemon - Markham, ON, Canada. ...   

                                             img_url     nr  photo_count  \
0  ['https://s3-media4.fl.yelpcdn.com/bphoto/tu7j...  False        325.0   
1  ['https://s3-media3.fl.yelpcdn.com/bphoto/h110...  False        307.0   

   stars  review_count_x          review_date               review_id  \
0    4.0             122  ['8', '23', '2016']  rqjzFEb1rQ09CgDVlGxZug   
1    3.0             114  ['10', '2', '2016']  P7S5VclOJEihkqpA7LscPw   

  review_language                                               text  \
0              en  I ordered the lemon mango slush and the lemon ...   
1              en  Came here on a Sunday afternoon, it wasn't bus...   

         ufc                 user_id                            user_loc  \
0  [1, 1, 1]  zsJFjhBQEFQ6gJ7BsNM_Ug                     Toronto, Canada   
1  [1, 0, 0]  P7YuMh74-I2cDq7oU8frww  York Regional Municipality, Canada   

   vote_count  Updated  Year  Day  Month  level_0  index  Unnamed: 0_y  \
0         1.0    False  2016   23      8     5733  21653         21653   
1         1.0    False  2016    2     10     5733  21653         21653   

                 alias                                         categories  \
0  happy-lemon-markham  [{'alias': 'bubbletea', 'title': 'Bubble Tea'}...   
1  happy-lemon-markham  [{'alias': 'bubbletea', 'title': 'Bubble Tea'}...   

                                         coordinates    display_phone  \
0  {'latitude': 43.8258200636421, 'longitude': -7...  +1 416-855-0768   
1  {'latitude': 43.8258200636421, 'longitude': -7...  +1 416-855-0768   

      distance                                          image_url  is_closed  \
0  2867.240253  https://s3-media4.fl.yelpcdn.com/bphoto/ATj6Mv...      False   
1  2867.240253  https://s3-media4.fl.yelpcdn.com/bphoto/ATj6Mv...      False   

                                            location         name  \
0  {'address1': 'B25 4300 Steeles Avenue E', 'add...  Happy Lemon   
1  {'address1': 'B25 4300 Steeles Avenue E', 'add...  Happy Lemon   

          phone price  business_stars  review_count_y transactions  \
0  1.416855e+10     $             3.5              32           []   
1  1.416855e+10     $             3.5              32           []   

                                                 url          latitude  \
0  https://www.yelp.com/biz/happy-lemon-markham?a...  43.8258200636421   
1  https://www.yelp.com/biz/happy-lemon-markham?a...  43.8258200636421   

           longitude        date  
0  -79.3063458055258  2016-08-23  
1  -79.3063458055258  2016-10-02

In [27]:
df = df.reset_index(drop=True)

In [28]:
len(df)

408836

In [29]:
dfff = df.copy()

change category format

In [30]:
#A list of categories
ans = []
for cat in tqdm(df.categories.values):
    temp = yaml.safe_load(cat)
#     ans.append([temp[i]["title"] for i in range(len(temp))])
    cat_str = ""
    #loop through key 
    for i in range(len(temp)):
        #if first element
        if i == 0:
            cat_str += temp[i]["title"]
            #if more than one title
            if len(temp) >1:
                cat_str += ", "
        #if last element
        elif i == len(temp)-1:
            cat_str += temp[i]["title"]
        else:
            cat_str += temp[i]["title"]
            cat_str += ", "
    ans.append(cat_str)
    

100%|████████████████████████████████████████████████████████████████████████| 408836/408836 [02:59<00:00, 2274.66it/s]


In [31]:
len(ans)

408836

In [32]:
arr_temp = np.asarray(ans)

In [33]:
df_cat = pd.DataFrame(arr_temp)
df_cat.rename(columns={0: "cat"}, inplace = True)

In [34]:
#df_cat[df_cat['cat'] == 'Caribbean']
#df[df['name'] == "Aunt Elsie's Carribean Kitchen"]
#df[df['categories'].str.contains('Caribbean',case=False)]

In [35]:
#Create a new column for the review df
df["cat"] = df_cat

In [36]:
pd.set_option('display.max_rows', 100000)

In [37]:
#Delete original categories column
del df['categories']

In [38]:
df.rename(columns={"cat": "categories"}, inplace = True)

In [39]:
df.head(2)

Unnamed: 0_x  Unnamed: 0.1             business_id  friend_count  ghost  \
0             6             6  Xo1LNzhnwE-ilqsM3ybs9Q           105  False   
1             7             7  Xo1LNzhnwE-ilqsM3ybs9Q           171  False   

                                             img_dsc  \
0  ['Photo of Happy Lemon - Markham, ON, Canada. ...   
1  ['Photo of Happy Lemon - Markham, ON, Canada. ...   

                                             img_url     nr  photo_count  \
0  ['https://s3-media4.fl.yelpcdn.com/bphoto/tu7j...  False        325.0   
1  ['https://s3-media3.fl.yelpcdn.com/bphoto/h110...  False        307.0   

   stars  review_count_x          review_date               review_id  \
0    4.0             122  ['8', '23', '2016']  rqjzFEb1rQ09CgDVlGxZug   
1    3.0             114  ['10', '2', '2016']  P7S5VclOJEihkqpA7LscPw   

  review_language                                               text  \
0              en  I ordered the lemon mango slush and the lemon ...   
1              en  Came here on a Sunday afternoon, it wasn't bus...   

         ufc                 user_id                            user_loc  \
0  [1, 1, 1]  zsJFjhBQEFQ6gJ7BsNM_Ug                     Toronto, Canada   
1  [1, 0, 0]  P7YuMh74-I2cDq7oU8frww  York Regional Municipality, Canada   

   vote_count  Updated  Year  Day  Month  level_0  index  Unnamed: 0_y  \
0         1.0    False  2016   23      8     5733  21653         21653   
1         1.0    False  2016    2     10     5733  21653         21653   

                 alias                                        coordinates  \
0  happy-lemon-markham  {'latitude': 43.8258200636421, 'longitude': -7...   
1  happy-lemon-markham  {'latitude': 43.8258200636421, 'longitude': -7...   

     display_phone     distance  \
0  +1 416-855-0768  2867.240253   
1  +1 416-855-0768  2867.240253   

                                           image_url  is_closed  \
0  https://s3-media4.fl.yelpcdn.com/bphoto/ATj6Mv...      False   
1  https://s3-media4.fl.yelpcdn.com/bphoto/ATj6Mv...      False   

                                            location         name  \
0  {'address1': 'B25 4300 Steeles Avenue E', 'add...  Happy Lemon   
1  {'address1': 'B25 4300 Steeles Avenue E', 'add...  Happy Lemon   

          phone price  business_stars  review_count_y transactions  \
0  1.416855e+10     $             3.5              32           []   
1  1.416855e+10     $             3.5              32           []   

                                                 url          latitude  \
0  https://www.yelp.com/biz/happy-lemon-markham?a...  43.8258200636421   
1  https://www.yelp.com/biz/happy-lemon-markham?a...  43.8258200636421   

           longitude        date                categories  
0  -79.3063458055258  2016-08-23  Bubble Tea, Coffee & Tea  
1  -79.3063458055258  2016-10-02  Bubble Tea, Coffee & Tea

In [40]:
print('#of reviews:', len(df))

#of reviews: 408836


In [41]:
#yaml.safe_load(df_business_clean.coordinates[0])

In [42]:
df_business_clean.head(2)

level_0  index  Unnamed: 0                    alias  \
0        0      0           0    the-ossington-toronto   
1        1      1           1  life-is-sweet-toronto-3   

                                          categories  \
0      [{'alias': 'divebars', 'title': 'Dive Bars'}]   
1  [{'alias': 'desserts', 'title': 'Desserts'}, {...   

                                         coordinates    display_phone  \
0      {'latitude': 43.6456, 'longitude': -79.41903}  +1 416-850-0161   
1  {'latitude': 43.67212500034, 'longitude': -79....  +1 416-698-0555   

      distance             business_id  \
0  4831.221092  KUdj08tVC3tvIT0rM6V8uQ   
1  1716.906703  rnjFHvb1I-KlnGvv_o_Zxg   

                                           image_url  is_closed  \
0  https://s3-media1.fl.yelpcdn.com/bphoto/dEQPAb...      False   
1  https://s3-media2.fl.yelpcdn.com/bphoto/s11QxZ...      False   

                                            location           name  \
0  {'address1': '61 Ossington Avenue', 'address2'...  The Ossington   
1  {'address1': '2345 Queen Street E', 'address2'...  Life is Sweet   

          phone price  rating  review_count transactions  \
0  1.416850e+10    $$     3.0            46           []   
1  1.416698e+10    $$     4.0            10           []   

                                                 url        latitude  \
0  https://www.yelp.com/biz/the-ossington-toronto...         43.6456   
1  https://www.yelp.com/biz/life-is-sweet-toronto...  43.67212500034   

         longitude  
0        -79.41903  
1  -79.28946080056

In [43]:
print('# of business', len(df_business_clean))

# of business 9377


In [44]:
#checking number of users
df.user_id

0         zsJFjhBQEFQ6gJ7BsNM_Ug
1         P7YuMh74-I2cDq7oU8frww
2         C91it8b3odRg0503asUaJA
3         dAB-v4B-5_8QgTcoVSnZOw
4         UxwiJpYSqOZJQzUMF6Xl6A
5         3AmCnDklEKOO3ERIrGFB4Q
6         9nA0Fe0GyX00GzIl7fn2eg
7         0U52n_sqA9j6UmB4mNVT9A
8         OXuToHJF6vYo3dxS7VYfWA
9         cA5objGauaX5BHYlzL0P8g
10        oK2IsMmz428wH6iB8tANFQ
11        G5IWhowNs3ge7YHT7_DR4g
12        Dt_h4Dt0lVblqRxLLV25YQ
13        SAeScmq3cxbikwnjyTqjxQ
14        XjkgUNYAqnVcuFmU53xP2Q
15        CxDOIDnH8gp9KXzpBHJYXw
16        L_OxAt1gt9l1gokgGoW7Sg
17        51_EJUsPW8NpsO8C9N4JqA
18        nMAq9WizgiDkZA11GrGLbA
19        DG1QPjVVsCcXiKP3xGh3pQ
20        pn_flI3EBNugBEYFp9okxQ
21        Mql2iMhK_5rS0Co5uRctFQ
22        26WgdHfEjWj4BrN-cUNhVw
23        7HFkF9A2xaHxLqwcFnJ0JQ
24        XbWP6vAli3waJ0iR_lcjOg
25        UC27mopi9fL9lVoSyonwSQ
26        Ylw1l9OqrzZEiltcEJly9Q
27        EiT_pSuIb08oRn4CfwfMJg
28        2e5V6M4GNufEnbGJpVdCjw
29        G_uHoVY0UIb3g4eNZP3lUQ
30        

In [46]:
set(df['categories'])

{'Specialty Food, Coffee & Tea, Juice Bars & Smoothies',
 'Breakfast & Brunch, Juice Bars & Smoothies, Organic Stores',
 'Vietnamese, Bubble Tea, Thai',
 'Specialty Food, Butcher',
 'Chocolatiers & Shops, Ice Cream & Frozen Yogurt',
 'Latin American, Fast Food',
 'Bistros, Breakfast & Brunch, French',
 'Venues & Event Spaces, Russian',
 'Bars, Indian',
 'Middle Eastern, Salad, Sandwiches',
 'Japanese, Fast Food',
 'Burgers, Ice Cream & Frozen Yogurt',
 'Coffee & Tea, Desserts, Bubble Tea',
 'Specialty Food, Bakeries, Desserts, Cafes',
 'Portuguese, Burgers, Breakfast & Brunch',
 'Breakfast & Brunch, Cocktail Bars',
 'Caterers, Pizza',
 'Halal, Asian Fusion',
 'Ice Cream & Frozen Yogurt, Desserts, Coffee & Tea',
 'Pizza, Falafel, Breakfast & Brunch',
 'Tapas Bars, Korean, Canadian (New)',
 'Bubble Tea, Tea Rooms',
 'Halal, Arabian, Middle Eastern',
 'Bars, African',
 'Chicken Wings, Barbeque, Pizza',
 'Belgian, Fast Food',
 'Delis, Meat Shops, Smokehouse',
 'Delis, Cheese Shops',
 'Dess

# Data Processing & Exporting data

In [140]:
Export = df.to_json(r'..\\data\\Cleaned_Toronto_Reviews.json', orient='records')

In [141]:
Export = df_business_clean.to_json(r'..\\data\\Cleaned_Toronto_Business.json', orient='records')

# Checking the export data

In [142]:
filename = "..\\data\\Cleaned_Toronto_Business.json"
with open(filename,'r') as f:
        data = f.readlines()
        data = list(map(json.loads, data))
    
data = data[0]
#Get all the data from the dggeata file
df = pd.DataFrame(data)

df.rename(columns={'stars': 'review_stars', 'text': 'review_text', 'cool': 'review_cool',
           'funny': 'review_funny', 'useful': 'review_useful'}, inplace=True)

In [143]:
df.head(5)

Unnamed: 0                                 alias             business_id  \
0           0                 the-ossington-toronto  KUdj08tVC3tvIT0rM6V8uQ   
1           1               life-is-sweet-toronto-3  rnjFHvb1I-KlnGvv_o_Zxg   
2           2                     subway-toronto-51  f8YPC7K4UUTkKatE5ga8Ig   
3           5             jodies-restaurant-toronto  K5TteBnAfgj18HRnV-Yy4w   
4          11  the-great-canadian-bagel-ltd-vaughan  ARwwcafc0x5s9wC-Te9yXg   

                                                                                  categories  \
0                                              [{'alias': 'divebars', 'title': 'Dive Bars'}]   
1   [{'alias': 'desserts', 'title': 'Desserts'}, {'alias': 'bakeries', 'title': 'Bakeries'}]   
2  [{'alias': 'sandwiches', 'title': 'Sandwiches'}, {'alias': 'hotdogs', 'title': 'Fast F...   
3  [{'alias': 'hotdogs', 'title': 'Fast Food'}, {'alias': 'diners', 'title': 'Diners'}, {...   
4                                                   [{'alias': 'bagels', 'title': 'Bagels'}]   

                                                      coordinates  \
0                   {'latitude': 43.6456, 'longitude': -79.41903}   
1      {'latitude': 43.67212500034, 'longitude': -79.28946080056}   
2                  {'latitude': 43.66449, 'longitude': -79.34116}   
3  {'latitude': 43.6053352355957, 'longitude': -79.5289154052734}   
4              {'latitude': 43.7928079, 'longitude': -79.5312639}   

     display_phone     distance  \
0  +1 416-850-0161  4831.221092   
1  +1 416-698-0555  1716.906703   
2  +1 416-465-8100  2934.260861   
3  +1 416-255-5552  4262.777626   
4  +1 905-760-9955  7595.423171   

                                                              image_url  \
0  https://s3-media1.fl.yelpcdn.com/bphoto/dEQPAbThPHKevj07OijSfA/o.jpg   
1  https://s3-media2.fl.yelpcdn.com/bphoto/s11QxZr-V8-VJHNLQJyvgQ/o.jpg   
2  https://s3-media1.fl.yelpcdn.com/bphoto/JpxU9FOgghpQQptpdsDDtg/o.jpg   
3  https://s3-media3.fl.yelpcdn.com/bphoto/GtkSIOchBTNry8WbIiZ7Gg/o.jpg   
4                                                                  None   

   index  is_closed          latitude  level_0  \
0      0      False           43.6456        0   
1      1      False    43.67212500034        1   
2      2      False          43.66449        2   
3      5      False  43.6053352355957        3   
4     11      False        43.7928079        4   

                                                                                    location  \
0  {'address1': '61 Ossington Avenue', 'address2': '', 'address3': '', 'city': 'Toronto',...   
1  {'address1': '2345 Queen Street E', 'address2': '', 'address3': '', 'city': 'Toronto',...   
2  {'address1': '331 Carlaw Avenue', 'address2': 'Unit 103', 'address3': '', 'city': 'Tor...   
3  {'address1': '331 Horner Avenue', 'address2': '', 'address3': '', 'city': 'Toronto', '...   
4  {'address1': '3300 Hwy 7', 'address2': 'Suite 101', 'address3': '', 'city': 'Vaughan',...   

           longitude                           name         phone price  \
0          -79.41903                  The Ossington  1.416850e+10    $$   
1    -79.28946080056                  Life is Sweet  1.416698e+10    $$   
2          -79.34116                         Subway  1.416466e+10    $$   
3  -79.5289154052734             Jodie's Restaurant  1.416256e+10    $$   
4        -79.5312639  The Great Canadian Bagel, Ltd  1.905761e+10    $$   

   rating  review_count transactions  \
0     3.0            46           []   
1     4.0            10           []   
2     1.5             6           []   
3     4.5             6           []   
4     4.0             1           []   

                                                                                         url  
0  https://www.yelp.com/biz/the-ossington-toronto?adjust_creative=uxtIWjm7I33oX3CDHUtQgQ&...  
1  https://www.yelp.com/biz/life-is-sweet-toronto-3?adjust_creative=9LfdvYfx0rVPnDmG5bc0i...  
2  https://www.yelp

In [ ]:
pd.set_option('display.max_columns', None)

In [144]:
set(df.categories.values)

{"[{'alias': 'hotdog', 'title': 'Hot Dogs'}, {'alias': 'sportsbars', 'title': 'Sports Bars'}, {'alias': 'beerbar', 'title': 'Beer Bar'}]",
 "[{'alias': 'italian', 'title': 'Italian'}, {'alias': 'pizza', 'title': 'Pizza'}, {'alias': 'sandwiches', 'title': 'Sandwiches'}]",
 "[{'alias': 'pizza', 'title': 'Pizza'}, {'alias': 'italian', 'title': 'Italian'}, {'alias': 'sandwiches', 'title': 'Sandwiches'}]",
 "[{'alias': 'pakistani', 'title': 'Pakistani'}, {'alias': 'bbq', 'title': 'Barbeque'}, {'alias': 'seafood', 'title': 'Seafood'}]",
 "[{'alias': 'cocktailbars', 'title': 'Cocktail Bars'}]",
 "[{'alias': 'coffee', 'title': 'Coffee & Tea'}, {'alias': 'breakfast_brunch', 'title': 'Breakfast & Brunch'}]",
 "[{'alias': 'filipino', 'title': 'Filipino'}, {'alias': 'desserts', 'title': 'Desserts'}, {'alias': 'popupshops', 'title': 'Pop-up Shops'}]",
 "[{'alias': 'personalchefs', 'title': 'Personal Chefs'}, {'alias': 'catering', 'title': 'Caterers'}]",
 "[{'alias': 'mediterranean', 'title': 'Medit

In [60]:
df[df['categories'].str.contains('Food Trucks')].categories.values

array(["[{'alias': 'venezuelan', 'title': 'Venezuelan'}, {'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'icecream', 'title': 'Ice Cream & Frozen Yogurt'}, {'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'southern', 'title': 'Southern'}, {'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'foodtrucks', 'title': 'Food Trucks'}, {'alias': 'japanese', 'title': 'Japanese'}, {'alias': 'asianfusion', 'title': 'Asian Fusion'}]",
       "[{'alias': 'bbq', 'title': 'Barbeque'}, {'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'gourmet', 'title': 'Specialty Food'}, {'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'foodtrucks', 'title': 'Food Trucks'}, {'alias': 'vegan', 'title': 'Vegan'}]",
       "[{'alias': 'catering', 'title': 'Caterers'}, {'alias': 'foodtrucks', 'title': 'Food Trucks'}]",
       "[{'alias': 'foodtrucks', 'title': 

In [49]:
len(df[df['longitude'] == 'None'])

0

In [148]:
filename = "..\\data\\Cleaned_Toronto_Reviews.json"
with open(filename,'r') as f:
        data = f.readlines()
        data = list(map(json.loads, data))
    
data = data[0]
#Get all the data from the dggeata file
df_reviews = pd.DataFrame(data)

In [149]:
df_reviews.head(2)

Day  Month  Unnamed: 0.1  Unnamed: 0_x  Unnamed: 0_y  Updated  Year  \
0   23      8             6             6         21653    False  2016   
1    2     10             7             7         21653    False  2016   

                 alias             business_id  business_stars  \
0  happy-lemon-markham  Xo1LNzhnwE-ilqsM3ybs9Q             3.5   
1  happy-lemon-markham  Xo1LNzhnwE-ilqsM3ybs9Q             3.5   

                 categories  \
0  Bubble Tea, Coffee & Tea   
1  Bubble Tea, Coffee & Tea   

                                                      coordinates        date  \
0  {'latitude': 43.8258200636421, 'longitude': -79.3063458055258}  2016-08-23   
1  {'latitude': 43.8258200636421, 'longitude': -79.3063458055258}  2016-10-02   

     display_phone     distance  friend_count  ghost  \
0  +1 416-855-0768  2867.240253           105  False   
1  +1 416-855-0768  2867.240253           171  False   

                                                              image_url  \
0  https://s3-media4.fl.yelpcdn.com/bphoto/ATj6Mv5Siz8ExZpAC8XSXA/o.jpg   
1  https://s3-media4.fl.yelpcdn.com/bphoto/ATj6Mv5Siz8ExZpAC8XSXA/o.jpg   

                                                                                     img_dsc  \
0                          ['Photo of Happy Lemon - Markham, ON, Canada. Lemon mango slush']   
1  ['Photo of Happy Lemon - Markham, ON, Canada. Oreo milk tea', 'Photo of Happy Lemon - ...   

                                                                                     img_url  \
0                ['https://s3-media4.fl.yelpcdn.com/bphoto/tu7jZIEA1RZJ6U1s7ZAx3w/348s.jpg']   
1  ['https://s3-media3.fl.yelpcdn.com/bphoto/h110aP3Vldr7KjuhOhryZQ/348s.jpg', 'https://s...   

   index  is_closed          latitude  level_0  \
0  21653      False  43.8258200636421     5749   
1  21653      False  43.8258200636421     5749   

                                                                                    location  \
0  {'address1': 'B25 4300 Steeles Avenue E', 'address2': '', 'address3': None, 'city': 'M...   
1  {'address1': 'B25 4300 Steeles Avenue E', 'address2': '', 'address3': None, 'city': 'M...   

           longitude         name     nr         phone  photo_count price  \
0  -79.3063458055258  Happy Lemon  False  1.416855e+10        325.0     $   
1  -79.3063458055258  Happy Lemon  False  1.416855e+10        307.0     $   

   review_count_x  review_count_y          review_date  \
0             122              32  ['8', '23', '2016']   
1             114              32  ['10', '2', '2016']   

                review_id review_language  stars  \
0  rqjzFEb1rQ09CgDVlGxZug              en    4.0   
1  P7S5VclOJEihkqpA7LscPw              en    3.0   

                                                                                        text  \
0  I ordered the lemon mango slush and the lemon taste is very strong.  If you love lemon...   
1  Came here on a Sunday afternoon, it wasn't busy at all. I came here for the Sunday spe...   

  transactions        ufc  \
0           []  [1, 1, 1]   
1           []  [1, 0, 0]   

                                                                                         url  \
0  https://www.yelp.com/biz/happy-lemon-markham?adjust_creative=ZbO96qTvvfSmFTkvkUBjkQ&ut...   
1  https://www.yelp.com/biz/happy-lemon-markham?adjust_creative=ZbO96qTvvfSmFTkvkUBjkQ&ut...   

                  user_id                            user_loc  vote_count  
0  zsJFjhBQEFQ6gJ7BsNM_Ug                     Toronto, Canada         1.0  
1  P7YuMh74-I2cDq7oU8frww  York Regional Municipality, Canada         1.0

In [154]:
print('number of users', len(set(df_reviews.user_id.values)))

number of users 95760


In [57]:
df_reviews[df_reviews['user_id'] == 'NaN']

Empty DataFrame
Columns: [Day, Month, Unnamed: 0.1, Unnamed: 0_x, Unnamed: 0_y, Updated, Year, alias, business_id, business_stars, categories, coordinates, date, display_phone, distance, friend_count, ghost, image_url, img_dsc, img_url, index, is_closed, latitude, level_0, location, longitude, name, nr, phone, photo_count, price, review_count_x, review_count_y, review_date, review_id, review_language, stars, text, transactions, ufc, url, user_id, user_loc, vote_count]
Index: []